<a href="https://colab.research.google.com/github/www6v/transformers-code/blob/master/%E2%80%9Cchatbot_lora_ipynb%E2%80%9D%E7%9A%84%E5%89%AF%E6%9C%AC.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Lora 实战

## Step1 导入相关包

In [ ]:
! pip install datasets transformers

In [ ]:
from datasets import Dataset
from transformers import AutoTokenizer, AutoModelForCausalLM, DataCollatorForSeq2Seq, TrainingArguments, Trainer
from datasets import load_dataset

## Step2 加载数据集

In [ ]:
# dataset_name = "abc"
# ds = Dataset.load_from_disk("../data/alpaca_data_zh/")
# ds = load_dataset("c-s-ale/alpaca-gpt4-data-zh", dataset_name)
ds = load_dataset("shibing624/alpaca-zh")
ds

DatasetDict({
    train: Dataset({
        features: ['instruction', 'input', 'output'],
        num_rows: 48818
    })
})

In [ ]:
# ds[:3]

## Step3 数据集预处理

In [ ]:
tokenizer = AutoTokenizer.from_pretrained("Langboat/bloom-1b4-zh")
tokenizer

BloomTokenizerFast(name_or_path='Langboat/bloom-1b4-zh', vocab_size=46145, model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='left', truncation_side='right', special_tokens={'bos_token': '<s>', 'eos_token': '</s>', 'unk_token': '<unk>', 'pad_token': '<pad>'}, clean_up_tokenization_spaces=False),  added_tokens_decoder={
	0: AddedToken("<unk>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	1: AddedToken("<s>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	2: AddedToken("</s>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	3: AddedToken("<pad>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
}

In [ ]:
def process_func(example):
    MAX_LENGTH = 256
    input_ids, attention_mask, labels = [], [], []
    instruction = tokenizer("\n".join(["Human: " + example["instruction"], example["input"]]).strip() + "\n\nAssistant: ")
    response = tokenizer(example["output"] + tokenizer.eos_token)
    input_ids = instruction["input_ids"] + response["input_ids"]
    attention_mask = instruction["attention_mask"] + response["attention_mask"]
    labels = [-100] * len(instruction["input_ids"]) + response["input_ids"]
    if len(input_ids) > MAX_LENGTH:
        input_ids = input_ids[:MAX_LENGTH]
        attention_mask = attention_mask[:MAX_LENGTH]
        labels = labels[:MAX_LENGTH]
    return {
        "input_ids": input_ids,
        "attention_mask": attention_mask,
        "labels": labels
    }

In [ ]:
ds.column_names['train']

['instruction', 'input', 'output']

In [ ]:
# tokenized_ds = ds.map(process_func, remove_columns=ds.column_names)
#tokenized_ds = ds.map(process_func)
tokenized_ds = ds.map(process_func, remove_columns=ds.column_names['train'])
tokenized_ds

DatasetDict({
    train: Dataset({
        features: ['input_ids', 'attention_mask', 'labels'],
        num_rows: 48818
    })
})

In [ ]:
tokenized_ds['train']

Dataset({
    features: ['input_ids', 'attention_mask', 'labels'],
    num_rows: 48818
})

In [ ]:
tokenized_ds['train']['input_ids']

[[26283,
  29,
  210,
  7160,
  28215,
  9905,
  15211,
  672,
  189,
  4340,
  17245,
  29,
  210,
  5040,
  584,
  7160,
  28215,
  9905,
  15211,
  1038,
  189,
  189,
  20,
  17,
  210,
  7160,
  9239,
  3365,
  420,
  9487,
  1965,
  15342,
  9239,
  6053,
  355,
  1227,
  32998,
  554,
  34487,
  1326,
  17632,
  355,
  975,
  5189,
  39177,
  6455,
  355,
  12144,
  17335,
  8481,
  355,
  1437,
  12785,
  6698,
  23294,
  672,
  189,
  21,
  17,
  210,
  22905,
  15356,
  420,
  9487,
  15597,
  22985,
  373,
  19320,
  554,
  18524,
  554,
  1229,
  6663,
  1467,
  642,
  16422,
  18235,
  27624,
  17520,
  8732,
  355,
  8729,
  1246,
  7110,
  554,
  1246,
  16422,
  642,
  15224,
  11367,
  355,
  718,
  7160,
  28215,
  15356,
  12577,
  672,
  189,
  22,
  17,
  210,
  20027,
  18399,
  420,
  20027,
  1079,
  15713,
  6455,
  21230,
  355,
  34810,
  9487,
  1688,
  8637,
  967,
  3958,
  210,
  43738,
  20027,
  420,
  15822,
  20027,
  12785,
  17374,
  12115,
  355,
 

In [ ]:
tokenized_ds['train']['input_ids']

[[26283,
  29,
  210,
  7160,
  28215,
  9905,
  15211,
  672,
  189,
  4340,
  17245,
  29,
  210,
  5040,
  584,
  7160,
  28215,
  9905,
  15211,
  1038,
  189,
  189,
  20,
  17,
  210,
  7160,
  9239,
  3365,
  420,
  9487,
  1965,
  15342,
  9239,
  6053,
  355,
  1227,
  32998,
  554,
  34487,
  1326,
  17632,
  355,
  975,
  5189,
  39177,
  6455,
  355,
  12144,
  17335,
  8481,
  355,
  1437,
  12785,
  6698,
  23294,
  672,
  189,
  21,
  17,
  210,
  22905,
  15356,
  420,
  9487,
  15597,
  22985,
  373,
  19320,
  554,
  18524,
  554,
  1229,
  6663,
  1467,
  642,
  16422,
  18235,
  27624,
  17520,
  8732,
  355,
  8729,
  1246,
  7110,
  554,
  1246,
  16422,
  642,
  15224,
  11367,
  355,
  718,
  7160,
  28215,
  15356,
  12577,
  672,
  189,
  22,
  17,
  210,
  20027,
  18399,
  420,
  20027,
  1079,
  15713,
  6455,
  21230,
  355,
  34810,
  9487,
  1688,
  8637,
  967,
  3958,
  210,
  43738,
  20027,
  420,
  15822,
  20027,
  12785,
  17374,
  12115,
  355,
 

In [ ]:
# tokenizer.decode(tokenized_ds[1]["input_ids"])
tokenizer.decode(tokenized_ds["train"][0]["input_ids"])

'Human: 保持健康的三个提示。\n\nAssistant: 以下是保持健康的三个提示：\n\n1. 保持身体活动。每天做适当的身体运动，如散步、跑步或游泳，能促进心血管健康，增强肌肉力量，并有助于减少体重。\n\n2. 均衡饮食。每天食用新鲜的蔬菜、水果、全谷物和脂肪含量低的蛋白质食物，避免高糖、高脂肪和加工食品，以保持健康的饮食习惯。\n\n3. 睡眠充足。睡眠对人体健康至关重要，成年人每天应保证 7-8 小时的睡眠。良好的睡眠有助于减轻压力，促进身体恢复，并提高注意力和记忆力。</s>'

In [ ]:
# tokenizer.decode(list(filter(lambda x: x != -100, tokenized_ds[1]["labels"])))
tokenizer.decode(list(filter(lambda x: x != -100, tokenized_ds["train"][0]["labels"])))

'以下是保持健康的三个提示：\n\n1. 保持身体活动。每天做适当的身体运动，如散步、跑步或游泳，能促进心血管健康，增强肌肉力量，并有助于减少体重。\n\n2. 均衡饮食。每天食用新鲜的蔬菜、水果、全谷物和脂肪含量低的蛋白质食物，避免高糖、高脂肪和加工食品，以保持健康的饮食习惯。\n\n3. 睡眠充足。睡眠对人体健康至关重要，成年人每天应保证 7-8 小时的睡眠。良好的睡眠有助于减轻压力，促进身体恢复，并提高注意力和记忆力。</s>'

## Step4 创建模型

In [ ]:
! pip install accelerate

In [ ]:
model = AutoModelForCausalLM.from_pretrained("Langboat/bloom-1b4-zh", low_cpu_mem_usage=True)
# model = AutoModelForCausalLM.from_pretrained("Langboat/bloom-1b4-zh")

In [ ]:
for name, parameter in model.named_parameters():
    print(name)

transformer.word_embeddings.weight
transformer.word_embeddings_layernorm.weight
transformer.word_embeddings_layernorm.bias
transformer.h.0.input_layernorm.weight
transformer.h.0.input_layernorm.bias
transformer.h.0.self_attention.query_key_value.weight
transformer.h.0.self_attention.query_key_value.bias
transformer.h.0.self_attention.dense.weight
transformer.h.0.self_attention.dense.bias
transformer.h.0.post_attention_layernorm.weight
transformer.h.0.post_attention_layernorm.bias
transformer.h.0.mlp.dense_h_to_4h.weight
transformer.h.0.mlp.dense_h_to_4h.bias
transformer.h.0.mlp.dense_4h_to_h.weight
transformer.h.0.mlp.dense_4h_to_h.bias
transformer.h.1.input_layernorm.weight
transformer.h.1.input_layernorm.bias
transformer.h.1.self_attention.query_key_value.weight
transformer.h.1.self_attention.query_key_value.bias
transformer.h.1.self_attention.dense.weight
transformer.h.1.self_attention.dense.bias
transformer.h.1.post_attention_layernorm.weight
transformer.h.1.post_attention_layernor

## Lora

### PEFT Step1 配置文件

In [ ]:
! pip install  peft

In [ ]:
from peft import LoraConfig, TaskType, get_peft_model

# config = LoraConfig(task_type=TaskType.CAUSAL_LM, target_modules=[".*\.1.*query_key_value"], modules_to_save=["word_embeddings"])
config = LoraConfig(task_type=TaskType.CAUSAL_LM, inference_mode=False, r=8, lora_alpha=32, lora_dropout=0.1)
config

LoraConfig(peft_type=<PeftType.LORA: 'LORA'>, auto_mapping=None, base_model_name_or_path=None, revision=None, task_type=<TaskType.CAUSAL_LM: 'CAUSAL_LM'>, inference_mode=False, r=8, target_modules=None, lora_alpha=32, lora_dropout=0.1, fan_in_fan_out=False, bias='none', modules_to_save=None, init_lora_weights=True, layers_to_transform=None, layers_pattern=None, rank_pattern={}, alpha_pattern={}, megatron_config=None, megatron_core='megatron.core', loftq_config={})

### PEFT Step2 创建模型

In [ ]:
model = get_peft_model(model, config)

In [ ]:
config

LoraConfig(peft_type=<PeftType.LORA: 'LORA'>, auto_mapping=None, base_model_name_or_path='Langboat/bloom-1b4-zh', revision=None, task_type=<TaskType.CAUSAL_LM: 'CAUSAL_LM'>, inference_mode=False, r=8, target_modules={'query_key_value'}, lora_alpha=32, lora_dropout=0.1, fan_in_fan_out=False, bias='none', modules_to_save=None, init_lora_weights=True, layers_to_transform=None, layers_pattern=None, rank_pattern={}, alpha_pattern={}, megatron_config=None, megatron_core='megatron.core', loftq_config={})

In [ ]:
for name, parameter in model.named_parameters():
    print(name)

base_model.model.transformer.word_embeddings.weight
base_model.model.transformer.word_embeddings_layernorm.weight
base_model.model.transformer.word_embeddings_layernorm.bias
base_model.model.transformer.h.0.input_layernorm.weight
base_model.model.transformer.h.0.input_layernorm.bias
base_model.model.transformer.h.0.self_attention.query_key_value.base_layer.weight
base_model.model.transformer.h.0.self_attention.query_key_value.base_layer.bias
base_model.model.transformer.h.0.self_attention.query_key_value.lora_A.default.weight
base_model.model.transformer.h.0.self_attention.query_key_value.lora_B.default.weight
base_model.model.transformer.h.0.self_attention.dense.weight
base_model.model.transformer.h.0.self_attention.dense.bias
base_model.model.transformer.h.0.post_attention_layernorm.weight
base_model.model.transformer.h.0.post_attention_layernorm.bias
base_model.model.transformer.h.0.mlp.dense_h_to_4h.weight
base_model.model.transformer.h.0.mlp.dense_h_to_4h.bias
base_model.model.tra

In [ ]:
model.print_trainable_parameters()

trainable params: 1,572,864 || all params: 1,304,684,544 || trainable%: 0.120555118647899


## Step5 配置训练参数

In [ ]:
pip install accelerate -U

In [ ]:
args = TrainingArguments(
    output_dir="./chatbot",
    per_device_train_batch_size=1,
    gradient_accumulation_steps=8,
    logging_steps=10,
    num_train_epochs=1
)

## Step6 创建训练器

In [ ]:
# trainer = Trainer(
#     model=model,
#     args=args,
#     train_dataset=tokenized_ds,
#     data_collator=DataCollatorForSeq2Seq(tokenizer=tokenizer, padding=True),
# )
trainer = Trainer(
    model=model,
    args=args,
    train_dataset=tokenized_ds["train"],
    data_collator=DataCollatorForSeq2Seq(tokenizer=tokenizer, padding=True),
)

## Step7 模型训练

In [ ]:
trainer.train()

You're using a BloomTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


## Step8 模型推理

In [ ]:
model = model.cuda()
ipt = tokenizer("Human: {}\n{}".format("考试有哪些技巧？", "").strip() + "\n\nAssistant: ", return_tensors="pt").to(model.device)
tokenizer.decode(model.generate(**ipt, max_length=128, do_sample=True)[0], skip_special_tokens=True)